In [15]:
import arxiv
import fitz  # PyMuPDF
import re
import random
import pandas as pd
import os
import arxiv_tool
import json
import arxiv_tool
import numpy as np
import copy
separator = "\n---SEPARATOR---\n"

# Dataset creation
Here the dataset for the classification (task2) was created and store into the folder task2/dataset 

To create the data the first paper is LLM-based NLG Evaluation: Current Status and Challenges with the number 2402.01383v1
First I download it from arxiv into a pdf.
Then is get the text of the paper and collect its references. The references are now the correct ones. Then some unrelated references need to be added. Then the llm has to identify the correct ones.

In [3]:
paper_id = "2402.01383v1"

In [4]:
paper = next(arxiv.Client().results(arxiv.Search(id_list=[paper_id])))

path = paper.download_pdf()

In [5]:
print(paper.title)
print(paper.summary)
raw = paper._raw
print(raw)
#paper.updated
print(paper.authors)
print(paper.published)

LLM-based NLG Evaluation: Current Status and Challenges
Evaluating natural language generation (NLG) is a vital but challenging
problem in artificial intelligence. Traditional evaluation metrics mainly
capturing content (e.g. n-gram) overlap between system outputs and references
are far from satisfactory, and large language models (LLMs) such as ChatGPT
have demonstrated great potential in NLG evaluation in recent years. Various
automatic evaluation methods based on LLMs have been proposed, including
metrics derived from LLMs, prompting LLMs, and fine-tuning LLMs with labeled
evaluation data. In this survey, we first give a taxonomy of LLM-based NLG
evaluation methods, and discuss their pros and cons, respectively. We also
discuss human-LLM collaboration for NLG evaluation. Lastly, we discuss several
open problems in this area and point out future research directions.
{'id': 'http://arxiv.org/abs/2402.01383v1', 'guidislink': True, 'link': 'http://arxiv.org/abs/2402.01383v1', 'updated':

In [6]:
full_text = arxiv_tool.get_full_text(path)
references_text = arxiv_tool.extract_references(full_text)
numbers = arxiv_tool.extract_arxiv_ids(references_text)

In [7]:
print(len(numbers))
df_all = pd.DataFrame({'arxiv_id': numbers})
 # Save the DataFrame to a CSV file
#df_all.to_csv('task2/dataset/'+paper_id+'_all.csv', index=False)

45


In [12]:
def create_json(ids):
    json_data = {}
    for id in ids:
        paper = next(arxiv.Client().results(arxiv.Search(id_list=[id])))
        json_data[id] = {'title':paper.title,'abstract':paper.summary,'date':paper.published.isoformat(),'label':1}  
    return json_data

data  = create_json(numbers)
#data

In [13]:
print(data['2305.10403']['date'])
print(data['2308.07201']['date'])
data['2305.10403']['date']<data['2308.07201']['date']

2023-05-17T17:46:53+00:00
2023-08-14T15:13:04+00:00


True

In [14]:
# These data will also be helpful in task3. Lets store them in task3/dataset
def write_to_json(json_data,file_name):
    with open(file_name+'.json', 'w') as file:
        json.dump(json_data, file, indent=4)
write_to_json(data,'task3/dataset/'+paper_id+'ref')

In [11]:
#Lets not forget that the original paper should also be stored
original_paper = {'id':paper_id,'title':paper.title,'abstract':paper.summary,'date':paper.published.isoformat(),'fulltext':full_text,'ref':numbers}
print(original_paper['title'])
write_to_json(original_paper,'task3/dataset/'+paper_id+'data')

LLM-based NLG Evaluation: Current Status and Challenges


In [ ]:
def add_unrelated(related_data,cut_date,query,num):
    all_data = {}
    client = arxiv.Client()
    search = arxiv.Search(
    query = query,
    max_results = num+10,
    # sort_by=arxiv.SortCriterion.SubmittedDate
    # sort_by = arxiv.SortCriterion.Relevance #Is default

    )

    results = list(client.results(search))
    # Lists to hold all IDs and their labels
    all_ids = []
    i = 0
    while len(all_ids)<num:
        result = results[i]
        arxiv_number = result.entry_id.split('/')[-1]
        arxiv_number = arxiv_number.split('v')[0]
        submission_date = result.published.isoformat()
        #check if already in list of sources (hence relevant) and before the overview
        if (arxiv_number not in related_data.keys()) and (submission_date<cut_date):
            all_ids.append(arxiv_number)
            all_data[arxiv_number] = {'title':result.title,'abstract':result.summary,'date':result.published.isoformat(),'label':0}  #No match/ label  0
        #print(submission_date)
        print(result.title)
        i+=1

    selected_numbers = random.sample(related_data.keys(), num)

    # Add matching IDs to the list
    for matching_id in selected_numbers:
        all_data[matching_id] = related_data[matching_id]


    keys = list(all_data.keys())
    random.shuffle(keys)

    # Create a new dictionary with shuffled keys
    shuffled_dict = {key: all_data[key] for key in keys}
    return shuffled_dict

sample_data = add_unrelated(data,original_paper['date'],'computer science',10)
sample_data


In [21]:
write_to_json(sample_data,'task2/dataset/'+paper_id)

In [ ]:
sample_data = add_unrelated(data,original_paper['date'],'computer science',len(data.keys()))
write_to_json(sample_data,'task2/dataset/'+paper_id+'all')

### Dataset with full text

In [7]:
def get_full_text(id):
    #Find paper in arxiv
    paper = next(arxiv.Client().results(arxiv.Search(id_list=[id])))
    # Download the PDF
    directory_path = './task/'+paper_id  
    os.makedirs(directory_path, exist_ok=True)
    pdf_path = paper.download_pdf(dirpath=directory_path)
    # Open the downloaded PDF
    document = fitz.open(pdf_path)

    # Extract text from each page
    text = ""
    for page_num in range(len(document)):
        page = document.load_page(page_num)
        text += page.get_text()
    return text

In [16]:
def create_dict_full_text(numbers,file_name):
    json_data = {}
    for number in numbers:
        text = get_full_text(number)
        json_data[number] = text
        print(number)
    with open(file_name+'.json', 'w') as file:
        json.dump(json_data, file, indent=4)
    return json_data
    
data = create_dict_full_text(numbers,'./task3/dataset/'+paper_id+'full_texts')

1606.06565
2305.10403
2306.04181
2308.07201
2310.00785
2210.11416
2309.15217
2302.04166
2311.00681
2312.10355
2309.13701
2310.00074
2303.07610
2310.00752
2311.18702
2310.08491
2309.13633
2311.00686
2310.19792
2310.05470
2310.19740
2307.02762
2310.01432
2311.09184
2305.14239
2305.14658
2309.13308
2307.07889
2303.15621
2310.15123
2206.05802
2311.09204
2307.09288
2305.17926
2308.04592
2310.11593
2306.05087
2309.12546
2307.03025
2307.10928
2401.00437
2312.15407
2308.01862
2306.05685
2310.17631


In [15]:
data

{'1606.06565': 'Concrete Problems in AI Safety\nDario Amodei∗\nGoogle Brain\nChris Olah∗\nGoogle Brain\nJacob Steinhardt\nStanford University\nPaul Christiano\nUC Berkeley\nJohn Schulman\nOpenAI\nDan Man´\ne\nGoogle Brain\nAbstract\nRapid progress in machine learning and artiﬁcial intelligence (AI) has brought increasing atten-\ntion to the potential impacts of AI technologies on society. In this paper we discuss one such\npotential impact: the problem of accidents in machine learning systems, deﬁned as unintended\nand harmful behavior that may emerge from poor design of real-world AI systems. We present a\nlist of ﬁve practical research problems related to accident risk, categorized according to whether\nthe problem originates from having the wrong objective function (“avoiding side eﬀects” and\n“avoiding reward hacking”), an objective function that is too expensive to evaluate frequently\n(“scalable supervision”), or undesirable behavior during the learning process (“safe exploration